In [1]:
print("OK")

OK


In [2]:
%pwd

'e:\\SOIS-Manipal\\Cloud_Computing\\GENAI\\GENAI Projects\\Medial_chat_bot\\ene-toend-mdeical-bot-allopathy-Ayurveda\\research'

In [3]:
import os 
os.chdir("../")

In [4]:
%pwd

'e:\\SOIS-Manipal\\Cloud_Computing\\GENAI\\GENAI Projects\\Medial_chat_bot\\ene-toend-mdeical-bot-allopathy-Ayurveda'

In [5]:
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [6]:
# Extract text from PDF files
def load_pdf_files(data):
    loader = DirectoryLoader(
        data,
        glob="*.pdf",
        loader_cls=PyPDFLoader
    )

    documents = loader.load()
    return documents

In [7]:
extracted_data = load_pdf_files(data='Data/')

In [8]:
extracted_data

[Document(metadata={'producer': 'PDFlib+PDI 5.0.0 (SunOS)', 'creator': 'PyPDF', 'creationdate': '2004-12-28T15:38:25-05:00', 'moddate': '2005-05-04T13:53:15-06:00', 'author': 'Clifford', 'enhanced': 'By PDF Enhancer 2.5/Win', 'spdf': '1096', 'source': 'Data\\gale-alternate-medicine.pdf', 'total_pages': 599, 'page': 0, 'page_label': '1'}, page_content='The GALE\nENCYCLOPEDIA of\nAlTERNATIVE\nMEDICINE\nSECOND EDITION\nGEAMv2htp/tp  10/11/04  10:45 AM  Page 1'),
 Document(metadata={'producer': 'PDFlib+PDI 5.0.0 (SunOS)', 'creator': 'PyPDF', 'creationdate': '2004-12-28T15:38:25-05:00', 'moddate': '2005-05-04T13:53:15-06:00', 'author': 'Clifford', 'enhanced': 'By PDF Enhancer 2.5/Win', 'spdf': '1096', 'source': 'Data\\gale-alternate-medicine.pdf', 'total_pages': 599, 'page': 1, 'page_label': '2'}, page_content='The GALE\nENCYCLOPEDIA of\nAlternative\nMEDICINE\nSECOND EDITION\nJACQUELINE L. LONGE, PROJECT EDITOR\nVOLUME\nD-K\n2\nGEAMv2htp/tp  10/11/04  10:45 AM  Page 3'),
 Document(metadata=

In [9]:
len(extracted_data)

1358

In [10]:
from typing import List
from langchain.schema import Document

def filter_to_minimal_docs(docs: List[Document]) -> List[Document]:
    """
    Given a list of Document objects, return a new list of Document objects
    containing only 'source' in metadata and the original page_content.
    """
    minimal_docs: List[Document] = []
    for doc in docs:
        src = doc.metadata.get("source")
        minimal_docs.append(
            Document(
                page_content=doc.page_content,
                metadata={"source": src}
            )
        )
    return minimal_docs

In [11]:
minimal_docs = filter_to_minimal_docs(extracted_data)

In [12]:
minimal_docs

[Document(metadata={'source': 'Data\\gale-alternate-medicine.pdf'}, page_content='The GALE\nENCYCLOPEDIA of\nAlTERNATIVE\nMEDICINE\nSECOND EDITION\nGEAMv2htp/tp  10/11/04  10:45 AM  Page 1'),
 Document(metadata={'source': 'Data\\gale-alternate-medicine.pdf'}, page_content='The GALE\nENCYCLOPEDIA of\nAlternative\nMEDICINE\nSECOND EDITION\nJACQUELINE L. LONGE, PROJECT EDITOR\nVOLUME\nD-K\n2\nGEAMv2htp/tp  10/11/04  10:45 AM  Page 3'),
 Document(metadata={'source': 'Data\\gale-alternate-medicine.pdf'}, page_content="The Gale Encyclopedia of Alternative Medicine, Second Edition\nProject Editor\nJacqueline L. Longe\nEditorial\nDeirdre S. Blanchfield, Laurie Fundukian, Erin\nWatts\nEditorial Support Services\nAndrea Lopeman\nRights Acquisition Management\nMargaret Abendroth, Ann T aylor\nImaging\nRandy Bassett, Lezlie Light, Dan W. Newell,\nRobyn V . Y oung\nProduct Design\nMichelle DiMercurio, T racey Rowens\nComposition and Electronic Prepress\nEvi Seoud, Mary Beth T rimper\nManufacturing\

In [13]:
# Split the documents into smaller chunks
def text_split(minimal_docs):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=500,
        chunk_overlap=20,
    )
    texts_chunk = text_splitter.split_documents(minimal_docs)
    return texts_chunk

In [14]:
texts_chunk = text_split(minimal_docs)
print(f"Number of chunks: {len(texts_chunk)}")

Number of chunks: 12672


In [15]:
texts_chunk

[Document(metadata={'source': 'Data\\gale-alternate-medicine.pdf'}, page_content='The GALE\nENCYCLOPEDIA of\nAlTERNATIVE\nMEDICINE\nSECOND EDITION\nGEAMv2htp/tp  10/11/04  10:45 AM  Page 1'),
 Document(metadata={'source': 'Data\\gale-alternate-medicine.pdf'}, page_content='The GALE\nENCYCLOPEDIA of\nAlternative\nMEDICINE\nSECOND EDITION\nJACQUELINE L. LONGE, PROJECT EDITOR\nVOLUME\nD-K\n2\nGEAMv2htp/tp  10/11/04  10:45 AM  Page 3'),
 Document(metadata={'source': 'Data\\gale-alternate-medicine.pdf'}, page_content='The Gale Encyclopedia of Alternative Medicine, Second Edition\nProject Editor\nJacqueline L. Longe\nEditorial\nDeirdre S. Blanchfield, Laurie Fundukian, Erin\nWatts\nEditorial Support Services\nAndrea Lopeman\nRights Acquisition Management\nMargaret Abendroth, Ann T aylor\nImaging\nRandy Bassett, Lezlie Light, Dan W. Newell,\nRobyn V . Y oung\nProduct Design\nMichelle DiMercurio, T racey Rowens\nComposition and Electronic Prepress\nEvi Seoud, Mary Beth T rimper\nManufacturing\

In [16]:
from langchain.embeddings import HuggingFaceEmbeddings

def download_embeddings():
    """
    Download and return the HuggingFace embeddings model.
    """
    model_name = "sentence-transformers/all-MiniLM-L6-v2"
    embeddings = HuggingFaceEmbeddings(
        model_name=model_name
    )
    return embeddings

embedding = download_embeddings()

C:\Users\MAHE\AppData\Local\Temp\ipykernel_10456\30168171.py:8: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embeddings = HuggingFaceEmbeddings(
e:\SOIS-Manipal\Cloud_Computing\GENAI\GENAI Projects\Medial_chat_bot\ene-toend-mdeical-bot-allopathy-Ayurveda\medical_env\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
e:\SOIS-Manipal\Cloud_Computing\GENAI\GENAI Projects\Medial_chat_bot\ene-toend-mdeical-bot-allopathy-Ayurveda\medical_env\Lib\site-packages\huggingface_hub\file_download.

In [17]:
embedding

HuggingFaceEmbeddings(client=SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
), model_name='sentence-transformers/all-MiniLM-L6-v2', cache_folder=None, model_kwargs={}, encode_kwargs={}, multi_process=False, show_progress=False)

In [18]:
vector = embedding.embed_query("Hello world")
vector

e:\SOIS-Manipal\Cloud_Computing\GENAI\GENAI Projects\Medial_chat_bot\ene-toend-mdeical-bot-allopathy-Ayurveda\medical_env\Lib\site-packages\torch\nn\modules\module.py:1762: FutureWarning: `encoder_attention_mask` is deprecated and will be removed in version 4.55.0 for `BertSdpaSelfAttention.forward`.
  return forward_call(*args, **kwargs)


[-0.03447727486491203,
 0.03102317824959755,
 0.006734970025718212,
 0.026108985766768456,
 -0.03936202451586723,
 -0.16030244529247284,
 0.06692401319742203,
 -0.006441489793360233,
 -0.0474504791200161,
 0.014758856035768986,
 0.07087527960538864,
 0.05552763119339943,
 0.019193334504961967,
 -0.026251312345266342,
 -0.01010954286903143,
 -0.02694045566022396,
 0.022307461127638817,
 -0.022226648405194283,
 -0.14969263970851898,
 -0.017493007704615593,
 0.00767625542357564,
 0.05435224249958992,
 0.0032543970737606287,
 0.031725890934467316,
 -0.0846213847398758,
 -0.02940601296722889,
 0.05159561336040497,
 0.04812406003475189,
 -0.0033148222137242556,
 -0.058279167860746384,
 0.04196927323937416,
 0.022210685536265373,
 0.1281888335943222,
 -0.022338971495628357,
 -0.011656315997242928,
 0.06292839348316193,
 -0.032876335084438324,
 -0.09122604131698608,
 -0.031175347045063972,
 0.0526994913816452,
 0.04703482985496521,
 -0.08420311659574509,
 -0.030056199058890343,
 -0.02074483036

In [19]:
print( "Vector length:", len(vector))

Vector length: 384


In [22]:
from dotenv import load_dotenv
import os
load_dotenv()

True

In [38]:
PINECONE_API_KEY = os.getenv("PINECONE_API_KEY")
OPENAI_API_KEY = os.getenv("OPENAI_API_KEY")


os.environ["PINECONE_API_KEY"] = PINECONE_API_KEY
os.environ["OPENAI_API_KEY"] = OPENAI_API_KEY

TypeError: str expected, not NoneType

In [26]:
from pinecone import Pinecone 
pinecone_api_key = PINECONE_API_KEY

pc = Pinecone(api_key=pinecone_api_key)

In [27]:
pc

In [28]:
from pinecone import ServerlessSpec 

index_name = "medical-chatbot"

if not pc.has_index(index_name):
    pc.create_index(
        name = index_name,
        dimension=384,  # Dimension of the embeddings
        metric= "cosine",  # Cosine similarity
        spec=ServerlessSpec(cloud="aws", region="us-east-1")
    )


index = pc.Index(index_name)

In [30]:
from langchain_pinecone import PineconeVectorStore

docsearch = PineconeVectorStore.from_documents(
    documents=texts_chunk,
    embedding=embedding,
    index_name=index_name
)

e:\SOIS-Manipal\Cloud_Computing\GENAI\GENAI Projects\Medial_chat_bot\ene-toend-mdeical-bot-allopathy-Ayurveda\medical_env\Lib\site-packages\torch\nn\modules\module.py:1762: FutureWarning: `encoder_attention_mask` is deprecated and will be removed in version 4.55.0 for `BertSdpaSelfAttention.forward`.
  return forward_call(*args, **kwargs)


In [31]:
# Load Existing index 

from langchain_pinecone import PineconeVectorStore
# Embed each chunk and upsert the embeddings into your Pinecone index.
docsearch = PineconeVectorStore.from_existing_index(
    index_name=index_name,
    embedding=embedding
)

# Add more data to the existing Pinecone index

In [32]:
dswith = Document(
    page_content="dswithbappy is a youtube channel that provides tutorials on various topics.",
    metadata={"source": "Youtube"}
)

In [33]:
docsearch.add_documents(documents=[dswith])

['49a90202-3abb-4e6e-b355-ffc397937219']

In [34]:
retriever = docsearch.as_retriever(search_type="similarity", search_kwargs={"k":3})

In [35]:
retrieved_docs = retriever.invoke("What is Aura therapy?")
retrieved_docs

e:\SOIS-Manipal\Cloud_Computing\GENAI\GENAI Projects\Medial_chat_bot\ene-toend-mdeical-bot-allopathy-Ayurveda\medical_env\Lib\site-packages\torch\nn\modules\module.py:1762: FutureWarning: `encoder_attention_mask` is deprecated and will be removed in version 4.55.0 for `BertSdpaSelfAttention.forward`.
  return forward_call(*args, **kwargs)


[Document(id='ddeb30af-a842-4598-986d-ea502f5f60c6', metadata={'source': 'Data\\The_GALE_ENCYCLOPEDIA_of_MEDICINE_SECOND.pdf'}, page_content='mines its characteristics.\nPotentize—The process of transferring the healing\nenergy of a plant into spring water.\nWindow—A perspective adopted to assess the\nproperty of a given plant.\npatients for such treatments on the strength of personal con-\nviction. However, it is difficult to discount the scores of tes-\ntimonials. Some practitioners refer skeptics to the research\nthat has been done regarding the “auras” of living things.\nTheoretically, the stronger the aura, the more alive an organ-'),
 Document(id='fb0525ca-bdc5-4849-afd5-f691500ff6cf', metadata={'source': 'Data\\gale-alternate-medicine.pdf'}, page_content='KEY TERMS\n . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . .\nAura—A light or radiance that is claimed to em-\nanate from the body and to be visible to certain\npersons with psychic or spiritual

In [36]:
from langchain_openai import ChatOpenAI

chatModel = ChatOpenAI(model="gpt-4o-mini")

OpenAIError: The api_key client option must be set either by passing api_key to the client or by setting the OPENAI_API_KEY environment variable

In [34]:
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate

In [35]:
system_prompt = (
    "You are an Medical assistant for question-answering tasks. "
    "Use the following pieces of retrieved context to answer "
    "the question. If you don't know the answer, say that you "
    "don't know. Use three sentences maximum and keep the "
    "answer concise."
    "\n\n"
    "{context}"
)


prompt = ChatPromptTemplate.from_messages(
    [
        ("system", system_prompt),
        ("human", "{input}"),
    ]
)

In [36]:
question_answer_chain = create_stuff_documents_chain(chatModel, prompt)
rag_chain = create_retrieval_chain(retriever, question_answer_chain)

In [37]:
response = rag_chain.invoke({"input": "what is Acromegaly and gigantism?"})
print(response["answer"])

Acromegaly is a disorder caused by the abnormal release of chemicals from the pituitary gland, leading to increased growth in bones and soft tissues. It occurs after bone growth has stopped. When this abnormality happens before growth stops, it results in gigantism, characterized by unusual height.


In [38]:
response = rag_chain.invoke({"input": "what is Acne?"})
print(response["answer"])

Acne is a common skin disease characterized by pimples on the face, chest, and back. It occurs when the skin's pores become clogged with oil, dead skin cells, and bacteria. The medical term for common acne is acne vulgaris.


In [39]:
response = rag_chain.invoke({"input": "what is the Treatment of Acne?"})
print(response["answer"])

The treatment of acne depends on its severity. For mild noninflammatory acne, topical treatments such as tretinoin, benzoyl peroxide, adapalene, or salicylic acid are recommended. For inflammatory acne, additional methods like topical antibiotics may be used, while severe cases may require treatments like isotretinoin.


In [40]:
response = rag_chain.invoke({"input": "what dswithbappy?"})
print(response["answer"])

dswithbappy is a YouTube channel that provides tutorials on various topics.
